# 金、银分析

当前数据集包括期货主力合约数据，上海现货数据。当前策略主要是金银比在历史极值附近的回归策略。--20181123

## 需要引入的库

In [1]:
#-*-coding:utf-8 -*-
import pandas as pd
import  numpy as np
import os
from datetime import datetime,timedelta
import matplotlib.pyplot as plt
from pyecharts import Line, Overlap,Grid

# 数据所在文件夹
future代表期货数据，
spot代表现货数据，
sh代表上海市场，
london代表伦敦市场。数据维护由其他程序承担，本分析程序仅进行分析

In [2]:
gold_future = "C:\\quanttime\\data\\gold\\sh_future\\gold.csv"
silver_future = "C:\\quanttime\\data\\gold\\sh_future\\silver.csv"
gold_spot = "C:\\quanttime\\data\\gold\\sh_spot\\gold.csv"
silver_spot = "C:\\quanttime\\data\\gold\\sh_spot\\silver.csv"

In [3]:
gold_future_data = pd.read_csv(gold_future, index_col=["date"])
silver_future_data = pd.read_csv(silver_future, index_col=["date"])

gold_spot_data = pd.read_csv(gold_spot, index_col=["date"])
gold_spot_data.index = pd.to_datetime(gold_spot_data.index)
silver_spot_data = pd.read_csv(silver_spot, index_col=["date"])
silver_spot_data.index = pd.to_datetime(silver_spot_data.index)

future_data = pd.merge(gold_future_data,silver_future_data,left_index=True,right_index=True,suffixes=('_gold','_silver'))
spot_data = pd.merge(gold_spot_data, silver_spot_data, left_index=True, right_index=True)
#spot_data["price_gold"] = pd.to_numeric(spot_data["price_gold"],downcast='float')
#spot_data["price_silver"] = pd.to_numeric(spot_data["price_silver"],downcast='float')

print(type(gold_spot_data.index))
print(type(silver_spot_data.index))


<class 'pandas.core.indexes.datetimes.DatetimeIndex'>
<class 'pandas.core.indexes.datetimes.DatetimeIndex'>


In [5]:
future_data.tail(5)

open_gold  close_gold  high_gold  low_gold  volume_gold  \
date                                                                  
2019-02-21     293.50       291.5     293.95    291.40     163306.0   
2019-02-22     291.25       289.6     291.90    289.35     160092.0   
2019-02-22     291.25       289.6     291.90    289.35     160092.0   
2019-02-22     291.25       289.6     291.90    289.35     160092.0   
2019-02-22     291.25       289.6     291.90    289.35     160092.0   

              money_gold  open_silver  close_silver  high_silver  low_silver  \
date                                                                           
2019-02-21  4.779593e+10       3765.0        3736.0       3787.0      3735.0   
2019-02-22  4.650848e+10       3730.0        3720.0       3743.0      3713.0   
2019-02-22  4.650848e+10       3730.0        3720.0       3743.0      3713.0   
2019-02-22  4.650848e+10       3730.0        3720.0       3743.0      3713.0   
2019-02-22  4.650848e+10       3730.0        3720.0       3743.0      3713.0   

            volume_silver  money_silver  
date                                     
2019-02-21       457394.0  2.579537e+10  
2019-02-22       369722.0  2.067434e+10  
2019-02-22       369722.0  2.067434e+10  
2019-02-22       369722.0  2.067434e+10  
2019-02-22       369722.0  2.067434e+10

In [61]:
spot_data.head(5)

price_gold  price_silver
date                                
2006-10-30      152.41        3374.0
2006-10-31      152.52        3373.0
2006-11-01      153.18        3398.0
2006-11-02      155.42        3419.0
2006-11-03      156.94        3387.0

In [6]:
spot_data["price_silver"]=pd.to_numeric(spot_data["price_silver"])
print(type(spot_data.iloc[0,0]))
print(type(spot_data.iloc[0,1]))

<class 'numpy.float64'>
<class 'numpy.float64'>


In [7]:
#del nan value
future_data = future_data.dropna()
spot_data = spot_data.dropna()
#print(data.head(5))

future_data["compare"] = future_data["close_gold"]/future_data["close_silver"]*1000
spot_data["compare"] = spot_data["price_gold"]/spot_data["price_silver"]*1000
spot_data["price_silver"] = spot_data["price_silver"]/10 #将银价按100g为单位计价，主要是与黄金价格在同一范围
spot_data = spot_data.round(2)

In [8]:
future_data_gold = np.array(future_data.loc[:, ["close_gold"]])
future_data_silver = np.array(future_data.loc[:,["close_silver"]])
future_data_compare = np.array(future_data.loc[: ,["compare"]])
future_datetime = np.array(future_data.index.map(str))


-----------------分界线--------------------
以下部分为图线，以上部分为数据准备

1、黄金期货主力合约图

In [9]:
line_future_gold = Line("future gold")
line_future_gold.add("future gold",future_datetime,future_data_gold.round(1),\
                     mark_point=["average","max","min"],\
                     is_datazoom_show=True,\
                    mark_point_symbol=None,\
                    yaxis_min=150,yaxis_max=300)
line_future_gold

2、白银期货主力合约图

In [10]:
line_future_silver = Line("future silver")
line_future_silver.add("future silver",future_datetime,future_data_silver,mark_point=["average","max","min"],is_datazoom_show=True)
line_future_silver

3、期货主力合约金银比及对比数据

In [11]:
line_future = Line("future AU/AG")
line_future.add("future gold",future_datetime,future_data_gold.round(1),\
                     mark_point=["average","max","min"]
                     )
line_future.add("future silver",future_datetime,future_data_silver,mark_point=["average","max","min"],is_datazoom_show=True,\
               datazoom_xaxis_index=[0,1],legend_top="50%")


line_future_compare = Line("future compare",title_top="50%")
line_future_compare.add("future AU/AG",future_datetime,future_data_compare.round(1),mark_point=["average","max","min"],is_datazoom_show=True
                       )

grid_future = Grid()
grid_future.add(line_future,grid_top="60%")
grid_future.add(line_future_compare,grid_bottom="60%")

4、期货主力合约金银比统计数据

In [101]:
future_data.loc[: ,["compare"]].describe()

compare
count  1593.000000
mean     65.770891
std       6.927213
min      49.084897
25%      60.799161
50%      67.237507
75%      70.901762
max      79.109977

In [107]:
future_data[["close_gold","close_silver","compare"]].sort_values(by=['compare'],ascending=False)

close_gold  close_silver    compare
date                                           
2018-11-21      279.10        3528.0  79.109977
2018-11-14      275.50        3489.0  78.962453
2018-11-15      277.05        3512.0  78.886674
2018-11-20      279.30        3541.0  78.876024
2018-11-12      276.55        3509.0  78.811627
2018-11-13      275.45        3499.0  78.722492
2018-11-16      277.50        3528.0  78.656463
2018-11-19      278.25        3539.0  78.623905
2016-03-01      263.05        3346.0  78.616258
2018-11-09      278.70        3549.0  78.529163
2018-09-17      267.35        3408.0  78.447770
2018-09-19      267.95        3418.0  78.393798
2018-09-07      267.20        3409.0  78.380757
2018-09-18      267.65        3416.0  78.351874
2018-09-14      268.65        3429.0  78.346457
2018-09-13      268.10        3422.0  78.345996
2016-02-29      259.40        3312.0  78.321256
2016-03-03      262.05        3347.0  78.293995
2018-09-12      266.80        3408.0  78.286385
2018-11-01      275.30        3520.0  78.210227
2018-09-05      265.60        3396.0  78.209658
2018-10-30      277.25        3545.0  78.208745
2018-09-10      266.25        3407.0  78.147931
2018-09-06      266.40        3410.0  78.123167
2016-03-02      259.85        3330.0  78.033033
2018-09-11      267.00        3423.0  78.001753
2018-10-31      274.90        3526.0  77.963698
2018-10-18      274.75        3529.0  77.854916
2018-11-07      275.90        3545.0  77.827927
2016-03-09      264.05        3396.0  77.753239
...                ...           ...        ...
2012-09-04      350.30        6876.0  50.945317
2012-10-09      361.80        7105.0  50.921886
2012-09-05      350.16        6879.0  50.902747
2012-09-07      349.61        6874.0  50.859761
2012-11-29      349.92        6881.0  50.853074
2012-10-08      361.38        7107.0  50.848459
2012-11-28      354.18        6967.0  50.836802
2012-10-12      359.95        7081.0  50.833216
2012-10-10      359.55        7078.0  50.798248
2012-11-27      356.55        7029.0  50.725566
2012-11-26      356.83        7036.0  50.714895
2012-12-18      347.37        6876.0  50.519197
2012-10-11      359.55        7120.0  50.498596
2012-09-13      356.13        7056.0  50.471939
2012-09-26      360.86        7150.0  50.469930
2012-11-30      352.08        6978.0  50.455718
2012-09-25      360.86        7159.0  50.406481
2012-09-24      360.12        7165.0  50.260991
2012-09-06      352.60        7043.0  50.063893
2012-09-12      357.89        7183.0  49.824586
2012-09-27      360.31        7234.0  49.807852
2012-09-11      357.78        7188.0  49.774624
2012-09-10      358.23        7213.0  49.664495
2012-09-18      361.87        7289.0  49.646042
2012-09-17      364.40        7352.0  49.564744
2012-09-28      365.48        7378.0  49.536460
2012-09-20      361.92        7307.0  49.530587
2012-09-14      365.19        7384.0  49.456934
2012-09-19      365.41        7435.0  49.147276
2012-09-21      363.67        7409.0  49.084897

[1593 rows x 3 columns]

前一次金银比回归分析。前一次金银比极值出现在2016-02-29	gold：259.40	silver：3312.0	AU/AG：78.321256

In [117]:
future_data_2016 = future_data.loc["2016-02-29":,["close_gold","close_silver","compare"]]
'''
取出从2016-2-29开始的后，第一个小于compare<70的索引
future_data_2016[future_data_2016.compare<70].index
'''
end = future_data_2016[future_data_2016.compare<70].index[0]

    

In [118]:
future_data_2016 = future_data.loc["2016-02-29":end, ["close_gold","close_silver","compare"]]
future_data_2016

close_gold  close_silver    compare
date                                           
2016-02-29      259.40        3312.0  78.321256
2016-03-01      263.05        3346.0  78.616258
2016-03-02      259.85        3330.0  78.033033
2016-03-03      262.05        3347.0  78.293995
2016-03-04      265.60        3426.0  77.524810
2016-03-07      265.65        3481.0  76.314278
2016-03-08      266.70        3450.0  77.304348
2016-03-09      264.05        3396.0  77.753239
2016-03-10      261.90        3391.0  77.233854
2016-03-11      265.75        3434.0  77.387886
2016-03-14      262.50        3433.0  76.463734
2016-03-15      257.85        3395.0  75.949926
2016-03-16      259.45        3404.0  76.219154
2016-03-17      263.30        3438.0  76.585224
2016-03-18      263.35        3521.0  74.794093
2016-03-21      259.70        3470.0  74.841499
2016-03-22      261.40        3516.0  74.345848
2016-03-23      258.35        3469.0  74.473912
2016-03-24      255.10        3409.0  74.831329
2016-03-25      256.10        3410.0  75.102639
2016-03-28      255.05        3406.0  74.882560
2016-03-29      255.75        3393.0  75.375774
2016-03-30      258.60        3424.0  75.525701
2016-03-31      256.15        3406.0  75.205520
2016-04-01      257.20        3421.0  75.182695
2016-04-05      256.05        3370.0  75.979228
2016-04-06      256.75        3371.0  76.164343
2016-04-07      256.45        3377.0  75.940184
2016-04-08      258.00        3380.0  76.331361
2016-04-11      260.55        3418.0  76.228789
2016-04-12      261.80        3467.0  75.511970
2016-04-13      260.40        3483.0  74.763135
2016-04-14      257.80        3485.0  73.974175
2016-04-15      257.20        3492.0  73.654066
2016-04-18      257.35        3484.0  73.866246
2016-04-19      259.85        3646.0  71.269885
2016-04-20      260.65        3679.0  70.848057
2016-04-21      264.00        3811.0  69.273157

在该时间段如果按照极值78回落到70区间，采用做空gold，做多相同价值合约的silver，区间获利计算如下：

In [142]:
gold_open = future_data.loc["2016-02-29",["close_gold"]]#gold 开仓价
gold_close = future_data.loc[end,["close_gold"]]#silver 结算价

silver_open = future_data.loc["2016-02-29",["close_silver"]]
silver_close = future_data.loc[end,["close_silver"]]

gold_total_value = gold_open.iloc[0] * 1000
silver_amount = round(gold_total_value /(silver_open.iloc[0] * 15))
silver_total_value = silver_open.iloc[0] * 15 * silver_amount

gold_return =  gold_total_value - gold_close.iloc[0] * 1000
silver_return =  silver_close.iloc[0] * 15 * silver_amount - silver_total_value
fact_return = silver_return - ( -gold_return)

print("===============================")
print("gold 开仓价格: %r, 平仓价格:%r"%(gold_open.iloc[0],gold_close.iloc[0]))
print("gold(short)total profit: %r"%gold_return)
print("silver 开仓价格: %r, 平仓价格:%r"%(silver_open.iloc[0],silver_close.iloc[0],))
print("silver(long) total profit: %r"%silver_return)
print("total return: %r"%fact_return)
print("total contract value:gold(%r),silver(%r)"%(gold_total_value.round(2),silver_total_value))
print("time consume: 2016-02-29-%r"%(end))
print("===============================")

gold 开仓价格: 259.39999999999998, 平仓价格:264.0
gold(short)total profit: -4600.0000000000291
silver 开仓价格: 3312.0, 平仓价格:3811.0
silver(long) total profit: 37425.0
total return: 32824.999999999971
total contract value:gold(259400.0),silver(248400.0)
time consume: 2016-02-29-'2016-04-21'


期货主力合约，金银比回归策略，期间最大回撤

In [151]:
future_data_2016["tmp_loss"] =  (gold_open.iloc[0] - future_data_2016["close_gold"]) * 1000 + \
                               (future_data_2016["close_silver"] - silver_open.iloc[0]) * 15 * silver_amount

loss_datetime = np.array(future_data_2016.index.map(str))
tmp_loss_value = np.array(future_data_2016.loc[:,["tmp_loss"]])
line_loss = Line("loss")
line_loss.add("loss",loss_datetime,tmp_loss_value.round(2),mark_point=["average","max","min"],is_stack=True)
line_loss

# 现货金银比分析

In [153]:
spot_data_gold = np.array(spot_data.loc[:,["price_gold"]])
spot_data_silver = np.array(spot_data.loc[:, ["price_silver"]])
spot_data_compare = np.array(spot_data.loc[:, ["compare"]])
spot_datatime = np.array(spot_data.index.map(str))

line_spot = Line("gold_sliver",title_top="50%")
line_spot_compare = Line("AU/AG")

line_spot.add("gold", spot_datatime, spot_data_gold, mark_point=["average","max","min"],legend_top="50%",is_stack=True,is_datazoom_show=True,\
               datazoom_xaxis_index=[0,1])
line_spot.add("silver",spot_datatime,spot_data_silver,mark_point=["average","max","min"],legend_top="50%",is_stack=True)
line_spot_compare.add("AU/AG",spot_datatime,spot_data_compare,mark_point=["average","max","min"],is_datazoom_show=True)

grid = Grid()
grid.add(line_spot,grid_top="60%")
#grid.add(line_silver,grid_top=300)
grid.add(line_spot_compare,grid_bottom="60%")


现货金银比的统计规律

In [155]:
spot_data["compare"].describe()

count    2625.000000
mean       59.149710
std         9.799567
min        29.730000
25%        51.010000
50%        61.110000
75%        67.430000
max        79.510000
Name: compare, dtype: float64

In [156]:
spot_data[["price_gold","price_silver","compare"]].sort_values(by=['compare'],ascending=False)

price_gold  price_silver  compare
date                                         
2016-03-01      260.94         328.2    79.51
2016-03-02      259.88         327.2    79.43
2016-03-03      260.34         328.4    79.28
2016-03-09      264.39         333.9    79.18
2016-02-29      258.26         327.1    78.95
2016-03-10      261.96         333.6    78.53
2016-03-04      263.21         335.4    78.48
2016-03-11      264.37         337.4    78.36
2016-03-08      265.81         339.3    78.34
2016-03-14      263.10         337.4    77.98
2008-12-30      192.81         247.4    77.93
2008-12-26      186.58         239.6    77.87
2008-12-29      193.82         249.0    77.84
2016-02-26      259.76         334.1    77.75
2016-03-07      265.09         341.0    77.74
2008-12-25      185.92         239.2    77.73
2008-12-24      185.21         238.7    77.59
2016-03-15      258.89         334.3    77.44
2016-02-25      260.21         336.3    77.37
2016-03-17      261.23         337.8    77.33
2008-12-31      190.90         246.9    77.32
2016-03-16      258.21         334.3    77.24
2016-04-08      257.57         333.5    77.23
2016-04-06      256.34         332.6    77.07
2016-04-11      259.15         337.2    76.85
2016-04-05      255.21         332.2    76.82
2016-04-07      255.47         332.7    76.79
2009-01-06      187.23         244.9    76.45
2016-03-29      255.39         334.3    76.40
2016-03-31      256.32         335.6    76.38
...                ...           ...      ...
2011-05-26      319.65         833.5    38.35
2011-05-31      320.70         838.6    38.24
2011-03-25      304.13         797.5    38.14
2011-07-19      332.50         872.0    38.13
2011-05-10      315.70         828.0    38.13
2011-03-30      300.78         789.3    38.11
2011-04-01      302.75         797.2    37.98
2011-03-31      301.42         797.3    37.81
2011-05-11      317.72         855.8    37.13
2011-05-05      318.32         863.6    36.86
2011-04-06      306.05         831.7    36.80
2011-04-07      306.88         835.7    36.72
2011-04-08      307.95         856.7    35.95
2011-04-12      307.99         866.9    35.53
2011-05-04      320.73         910.3    35.23
2011-04-13      307.14         873.6    35.16
2011-04-11      310.05         890.3    34.83
2011-04-14      307.78         885.4    34.76
2011-04-15      309.85         912.0    33.97
2011-04-18      311.89         922.8    33.80
2011-04-19      313.05         931.8    33.60
2011-04-20      314.50         957.3    32.85
2011-05-03      322.38         984.5    32.75
2011-04-27      315.91         980.9    32.21
2011-04-26      315.61         990.0    31.88
2011-04-21      315.82         992.8    31.81
2011-04-22      316.27        1009.9    31.32
2011-04-28      319.47        1049.8    30.43
2011-04-29      320.35        1056.2    30.33
2011-04-25      317.73        1068.6    29.73

[2625 rows x 3 columns]

期货主力合约与现货，2016-3月段，金银比比较

In [165]:
future_data_201603 = future_data.loc["2016-02-15":"2016-12-31",["close_gold","close_silver","compare"]]
spot_data_201603 = spot_data.loc["2016-02-15":"2016-12-31",["price_gold","price_silver","compare"]]
compare_201603 = pd.merge(future_data_201603,spot_data_201603,left_index=True,right_index=True,suffixes=["_future","_spot"])
datatime_201603 = np.array(compare_201603.index.map(str))
compare_future_201603 = np.array(compare_201603.loc[:,["compare_future"]])
compare_spot_201603 = np.array(compare_201603.loc[:,["compare_spot"]])

line_compare_201603 = Line("compare_201603")
line_compare_201603.add("compare_future",datatime_201603,compare_future_201603.round(2),mark_point=["average","max","min"],\
                        is_stack=True,is_datazoom_show=True,yaxis_min=30,yaxis_max=90)
line_compare_201603.add("compare_spot",datatime_201603,compare_spot_201603,mark_point=["average","max","min"],\
                        is_datazoom_show=True,yaxis_min=30,yaxis_max=90)
line_compare_201603